In [1]:
%%capture
!pip install datasets==1.4.1
!pip install transformers
!pip install torchaudio
!pip install librosa
!pip install jiwer
!pip install pydub==0.25.1

In [2]:
import os, sys
import torch
import torchaudio
import librosa
import numpy as np
from transformers import Wav2Vec2Processor, Wav2Vec2ForCTC
from pydub import AudioSegment

In [3]:
from google.colab import drive
drive.mount('/content/drive/')

Mounted at /content/drive/


In [ ]:
use_device = torch.device("cpu")
model = Wav2Vec2ForCTC.from_pretrained("/content/drive/MyDrive/machine-learning/speech-to-text/huggingface/pytorch/finetuning/dataset-comparison/wav2vec2-xlsr/checkpoint-141200").to(use_device)
processor = Wav2Vec2Processor.from_pretrained("/content/drive/MyDrive/machine-learning/speech-to-text/huggingface/pytorch/finetuning/dataset-comparison/wav2vec2-xlsr/processor")

In [ ]:
audio_path = "/content/drive/MyDrive/machine-learning/speech-to-text/data/predict/id/testing_1.wav"
filename = os.path.basename(audio_path)
audio_filename = filename.split(".")[0]
audio_format = filename.split(".")[1]
audio = AudioSegment.from_file_using_temporary_files(audio_path, format=audio_format)
audio_filename = str("/content/") + str(audio_filename) + ".mp3"
audio.export(audio_filename, format="mp3", parameters=["-ac", "1", "-ar", "16000"])

In [ ]:
def resample(speech_array, sampling_rate):
    if sampling_rate == 48000:
        speech_array = librosa.resample(np.asarray(speech_array), 48_000, 16_000)

    elif sampling_rate == 44100:
        speech_array = librosa.resample(np.asarray(speech_array), 44100, 16_000)

    elif sampling_rate == 32000:
        speech_array = librosa.resample(np.asarray(speech_array), 32000, 16_000)
    return speech_array

In [ ]:
speech_array, sampling_rate = torchaudio.load(audio_filename)
speech_array = resample(speech_array[0].numpy(), sampling_rate)
input_values = processor(speech_array, sampling_rate=16_000).input_values[0]
input_dict = processor(input_values, return_tensors="pt", padding=True)

In [ ]:
logits = model(input_dict.input_values.to(use_device)).logits
pred_ids = torch.argmax(logits, dim=-1)[0]
text = processor.decode(pred_ids)
print(text)

In [ ]:
import torch
from transformers import Wav2Vec2ForCTC, Wav2Vec2Processor
from torchaudio.transforms import Resample
from IPython.display import Audio
from pydub import AudioSegment

# Ganti dengan jalur file model hasil fine-tuning
fine_tuned_model_path = "path_to_your_fine_tuned_model"

# Load the processor and fine-tuned model
processor = Wav2Vec2Processor.from_pretrained(fine_tuned_model_path)
model = Wav2Vec2ForCTC.from_pretrained(fine_tuned_model_path)

# Load the audio file in mp3 format
mp3_audio_file_path = "path_to_your_audio_file.mp3"
audio = AudioSegment.from_file(mp3_audio_file_path, format="mp3")

# Resample the audio if needed
waveform, sample_rate = torch.tensor(audio.raw_data).to(torch.float32), audio.frame_rate
if sample_rate != processor.feature_extractor.sampling_rate:
    resampler = Resample(orig_freq=sample_rate, new_freq=processor.feature_extractor.sampling_rate)
    waveform = resampler(waveform)

# Tokenize and transcribe
input_values = processor(waveform.numpy(), return_tensors="pt", padding="longest").input_values
with torch.no_grad():
    logits = model(input_values).logits
    predicted_ids = torch.argmax(logits, dim=-1)

# Decode the predicted transcription
transcription = processor.batch_decode(predicted_ids)[0]
print("Predicted Transcription:", transcription)

# Play the original mp3 audio
Audio(mp3_audio_file_path)
